# Assignment 3: Non-Linear Models and Validation Metrics

Name: Christian Valdez 

In [1]:
# import libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
# dataset
import yellowbrick
from yellowbrick.datasets import load_spam, load_concrete

In [3]:
# sklearn
from sklearn.tree import DecisionTreeRegressor, plot_tree
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.model_selection import train_test_split, cross_validate
from sklearn.linear_model import LinearRegression
from sklearn.metrics import make_scorer, mean_squared_error, r2_score

## Part 1: Regression (14.5 marks)

### Step 1: Data Input (0.5 marks)

The data used for this task can be downloaded using the yellowbrick library: 
https://www.scikit-yb.org/en/latest/api/datasets/concrete.html

In [4]:
# import concrete dataset
X, y = yellowbrick.datasets.loaders.load_concrete(
    data_home=None, return_dataset=False)

In [5]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1030 entries, 0 to 1029
Data columns (total 8 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   cement  1030 non-null   float64
 1   slag    1030 non-null   float64
 2   ash     1030 non-null   float64
 3   water   1030 non-null   float64
 4   splast  1030 non-null   float64
 5   coarse  1030 non-null   float64
 6   fine    1030 non-null   float64
 7   age     1030 non-null   int64  
dtypes: float64(7), int64(1)
memory usage: 64.5 KB


### Step 3: Implement Machine Learning Model

### Step 4: Validate Model

Calculate the average training and validation accuracy using mean squared error with cross-validation. To do this, you will need to set `scoring='neg_mean_squared_error'` in your `cross_validate` function and negate the results (multiply by -1)

### Step 5: Visualize Results (4 marks)

1. Create a pandas DataFrame `results` with columns: Training accuracy and Validation accuracy, and index: DT, RF and GB
2. Add the accuracy results to the `results` DataFrame
3. Print `results`

In [6]:
# split data
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=0)

In [7]:
"""
    Step 3:
        1. Import models (all imports at the top)
        2. Instantiate models, max_Depth=5
        3. Train model
"""

# decision tree, max depth = 5
tree = DecisionTreeRegressor(max_depth=5, random_state=0)

# random forest, max depth = 5
rf = RandomForestRegressor(max_depth=5, random_state=0)

# gradient boosting, max depth = 5
gbm = GradientBoostingRegressor(max_depth=5, random_state=0)

# list of models
model_list = [tree, rf, gbm]

for model in model_list:
    model.fit(X_train, y_train)

In [8]:
# For plotting
fig, axes = plt.subplots(nrows=3, ncols=1, figsize=(10, 30), dpi=900)  # Change to 3x1 grid

# Decision Tree
plot_tree(tree, filled=True, ax=axes[0])  # Refer to the first subplot
axes[0].set_title('Decision Tree')

# Random Forest - plot the first tree in the forest
plot_tree(rf.estimators_[0], filled=True, ax=axes[1])  # Refer to the second subplot
axes[1].set_title('Random Forest')

# Gradient Boosting - plot the first tree
plot_tree(gbm.estimators_[0, 0], filled=True, ax=axes[2])  # Refer to the third subplot
axes[2].set_title('Gradient Boosting')

plt.tight_layout()  # To ensure subplots do not overlap
plt.show()

In [9]:
# re instantiate models
tree = DecisionTreeRegressor(max_depth=5, random_state=0)
rf = RandomForestRegressor(max_depth=5, random_state=0)
gbm = GradientBoostingRegressor(max_depth=5, random_state=0)

# list of models
model_list = [tree, rf, gbm]

In [10]:
# re instantiate models
tree = DecisionTreeRegressor(max_depth=5, random_state=0)
rf = RandomForestRegressor(max_depth=5, random_state=0)
gbm = GradientBoostingRegressor(max_depth=5, random_state=0)

# list of models
model_list = [tree, rf, gbm]

In [11]:
"""
    Step 4:
        1. Cross-validation
        2. Set scoring = neg_mean_squared_error
        3. Negate training_score

    Note: I used the entire dataset during my cross-validation.
"""

# cross-validation with 5 folds, scoring='neg_mean_squared_error'

results_trees = {
    "MSE Train Average": [],
    "MSE Test Average": [],
    "R2 Train Average": [],
    "R2 Test Average": [],
}

model_names = ["DT", "RF", "GB"]

for model in model_list:
    scores = cross_validate(model, X, y, cv=5, scoring="neg_mean_squared_error", return_train_score=True)
    training_score = scores["train_score"].mean()*-1
    testing_score = scores["test_score"].mean()*-1

    results_trees["MSE Train Average"].append(training_score)
    results_trees["MSE Test Average"].append(testing_score)

In [12]:
# re instantiate models
tree = DecisionTreeRegressor(max_depth=5, random_state=0)
rf = RandomForestRegressor(max_depth=5, random_state=0)
gbm = GradientBoostingRegressor(max_depth=5, random_state=0)

# list of models
model_list = [tree, rf, gbm]

In [13]:
"""
        1. Cross-validation
        2. Set scoring = r2
        3. Negate training_score

    Note: I used the entire dataset during my cross-validation.
"""

# cross-validation with 5 folds, scoring='r2'

for model in model_list:
    scores = cross_validate(model, X, y, cv=5, scoring="r2", return_train_score=True)
    training_score = scores["train_score"].mean()
    testing_score = scores["test_score"].mean()

    results_trees["R2 Train Average"].append(training_score)
    results_trees["R2 Test Average"].append(testing_score)

In [14]:
results_trees_df = pd.DataFrame(results_trees)
results_trees_df.index = model_names
results_trees_df

MSE Train Average  MSE Test Average  R2 Train Average  R2 Test Average
DT          47.918561        163.087775          0.822887         0.176210
RF          32.055432        156.404972          0.881221         0.173748
GB           3.739270         99.360259          0.986436         0.473701

In [15]:
"""
    Liner Regression
"""

linear_model = LinearRegression()
linear_model.fit(X_train, y_train)

# make predictions
linear_prediction_train = linear_model.predict(X_train)
linear_prediction_test = linear_model.predict(X_test)

# evaluate the model
mse_train = mean_squared_error(y_train, linear_prediction_train)
mse_test = mean_squared_error(y_test, linear_prediction_test)
r2_train = r2_score(y_train, linear_prediction_train)
r2_test = r2_score(y_test, linear_prediction_test)

results_lr = {
    "Training Accuracy": [mse_train, r2_train],
    "Validation Accuracy": [mse_test, r2_test]
}
results_lr = pd.DataFrame(results_lr)
results_lr.index = ["MSE", "R2 Score"]

results_lr

Training Accuracy  Validation Accuracy
MSE              111.358439            95.904136
R2 Score           0.610823             0.623414

### Questions (6 marks)
1. How do these results compare to the results using a linear model in the previous assignment? Use values.
1. Out of the models you tested, which model would you select for this dataset and why?
1. If you wanted to increase the accuracy of the tree-based models, what would you do? Provide two suggestions.

*ANSWER HERE*

### Process Description (4 marks)
Please describe the process you used to create your code. Cite any websites or generative AI tools used. You can use the following questions as guidance:
1. Where did you source your code?
1. In what order did you complete the steps?
1. If you used generative AI, what prompts did you use? Did you need to modify the code at all? Why or why not?
1. Did you have any challenges? If yes, what were they? If not, what helped you to be successful?

*DESCRIBE YOUR PROCESS HERE*

## Part 2: Classification (17.5 marks)

### Step 1: Data Input (2 marks)

The data used for this task can be downloaded from UCI: https://archive.ics.uci.edu/dataset/109/wine

Use the pandas library to load the dataset. You must define the column headers if they are not included in the dataset 

You will need to split the dataset into feature matrix `X` and target vector `y`. Which column represents the target vector?

Print the size and type of `X` and `y`

In [16]:
# import wine dataset
from ucimlrepo import fetch_ucirepo 

In [28]:
# SVC 
from sklearn.svm import SVC

# Decision Tree Classifier
from sklearn.tree import DecisionTreeClassifier

In [18]:
# fetch dataset 
wine = fetch_ucirepo(id=109) 
  
# data (as pandas dataframes) 
X = wine.data.features 
y = wine.data.targets 
  
# metadata 
print(wine.metadata) 
  
# variable information 
print(wine.variables) 

{'uci_id': 109, 'name': 'Wine', 'repository_url': 'https://archive.ics.uci.edu/dataset/109/wine', 'data_url': 'https://archive.ics.uci.edu/static/public/109/data.csv', 'abstract': 'Using chemical analysis to determine the origin of wines', 'area': 'Physical Science', 'tasks': ['Classification'], 'characteristics': ['Tabular'], 'num_instances': 178, 'num_features': 13, 'feature_types': ['Integer', 'Real'], 'demographics': [], 'target_col': ['class'], 'index_col': None, 'has_missing_values': 'no', 'missing_values_symbol': None, 'year_of_dataset_creation': 1992, 'last_updated': 'Mon Aug 28 2023', 'dataset_doi': '10.24432/C5PC7J', 'creators': ['Stefan Aeberhard', 'M. Forina'], 'intro_paper': {'title': 'Comparative analysis of statistical pattern recognition methods in high dimensional settings', 'authors': 'S. Aeberhard, D. Coomans, O. Vel', 'published_in': 'Pattern Recognition', 'year': 1994, 'url': 'https://www.semanticscholar.org/paper/83dc3e4030d7b9fbdbb4bde03ce12ab70ca10528', 'doi': '

In [48]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=0)

### Step 2: Data Processing (1.5 marks)

In [19]:
print("First 5 rows of the dataset")
X.head(5)

First 5 rows of the dataset


Alcohol  Malicacid   Ash  Alcalinity_of_ash  Magnesium  Total_phenols  \
0    14.23       1.71  2.43               15.6        127           2.80   
1    13.20       1.78  2.14               11.2        100           2.65   
2    13.16       2.36  2.67               18.6        101           2.80   
3    14.37       1.95  2.50               16.8        113           3.85   
4    13.24       2.59  2.87               21.0        118           2.80   

   Flavanoids  Nonflavanoid_phenols  Proanthocyanins  Color_intensity   Hue  \
0        3.06                  0.28             2.29             5.64  1.04   
1        2.76                  0.26             1.28             4.38  1.05   
2        3.24                  0.30             2.81             5.68  1.03   
3        3.49                  0.24             2.18             7.80  0.86   
4        2.69                  0.39             1.82             4.32  1.04   

   0D280_0D315_of_diluted_wines  Proline  
0                          3.92     1065  
1                          3.40     1050  
2                          3.17     1185  
3                          3.45     1480  
4                          2.93      735

In [49]:
print("Corresponding labels")
y.head(5)

Corresponding labels


class
0      1
1      1
2      1
3      1
4      1

In [50]:
# check for missing values
missing_values_X = X.isnull().sum().sum()
missing_values_y = y.isnull().sum()
missing_values_y = int(missing_values_y.sum())

if missing_values_X != 0:
    X.fillna(0, inplace=True)
    print(f"Filled missing values in X. Total filled: {missing_values_X}")
else:
    print("There are no missing values in X.")

if missing_values_y != 0:
    y.fillna(0, inplace=True)
    print(f"Filled missing values in y. Total filled: {missing_values_y}")
else:
    print("There are no missing values in y.")

There are no missing values in X.
There are no missing values in y.


In [22]:
# get num of wines
print("The following shows all the unique wines with their counts:")
y.value_counts()

The following shows all the unique wines with their counts:


class
2        71
1        59
3        48
Name: count, dtype: int64

### Step 3: Implement Machine Learning Model

In [51]:
"""
    Step 3:
        1. Import models
        2. Instantiate models
        3. Train models
"""

# instantiate SVC, linear, random state = 0
svc = SVC(kernel="linear", random_state=0)

# instantiate DTC, max depth = 3, random state = 0
dtc = DecisionTreeClassifier(max_depth=3, random_state=0)

model_list = [svc, dtc]

for model in model_list:
    model.fit(X_train, y_train)

c:\Users\chris\anaconda3\envs\ensf-ml\Lib\site-packages\sklearn\utils\validation.py:1184: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


### Step 4: Validate Model

In [56]:
# re instantiate models
svc = SVC(random_state=0)
dtc = DecisionTreeClassifier(max_depth=3, random_state=0)
model_list = [svc, dtc]

In [57]:
"""
    Step 4:
        1. Cross validation
        2. score=accuracy
"""

results_classifier = {
    "Train Average": [],
    "Test Average": [],
}

model_names = ["SVC", "DTC"]

for model in model_list:
    scores = cross_validate(model, X_train, y_train, cv=5, scoring="accuracy", return_train_score=True)

    training_score = scores["train_score"].mean()
    testing_score = scores["test_score"].mean()

    results_classifier["Train Average"].append(training_score)
    results_classifier["Test Average"].append(testing_score)

c:\Users\chris\anaconda3\envs\ensf-ml\Lib\site-packages\sklearn\utils\validation.py:1184: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\chris\anaconda3\envs\ensf-ml\Lib\site-packages\sklearn\utils\validation.py:1184: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\chris\anaconda3\envs\ensf-ml\Lib\site-packages\sklearn\utils\validation.py:1184: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\chris\anaconda3\envs\ensf-ml\Lib\site-packages\sklearn\utils\validation.py:1184: DataConversionWarning: A column-vector y was passed when a 1d array was e

### Step 5: Visualize Results (4 marks)

In [58]:
"""
    Step 5:
        1. Store results in df
"""

results_classifier_df = pd.DataFrame(results_classifier)
results_classifier_df.index = model_names
results_classifier_df

Train Average  Test Average
SVC       0.680427      0.676638
DTC       0.994357      0.894017

#### Step 5.2: Visualize Classification Errors
Which method gave the highest accuracy? Use this method to print the confusion matrix and classification report:

In [24]:
# TO DO: Implement best model

In [25]:
# TO DO: Print confusion matrix using a heatmap

In [26]:
# TO DO: Print classification report

### Questions (6 marks)
1. How do the training and validation accuracy change depending on the method used? Explain with values.
1. What are two reasons why the support vector machines model did not work as well as the tree-based model?
1. How many samples were incorrectly classified in step 5.2? 
1. In this case, is maximizing precision or recall more important? Why?

*YOUR ANSWERS HERE*

### Process Description (4 marks)
Please describe the process you used to create your code. Cite any websites or generative AI tools used. You can use the following questions as guidance:
1. Where did you source your code?
1. In what order did you complete the steps?
1. If you used generative AI, what prompts did you use? Did you need to modify the code at all? Why or why not?
1. Did you have any challenges? If yes, what were they? If not, what helped you to be successful?

*DESCRIBE YOUR PROCESS HERE*

## Part 3: Observations/Interpretation (3 marks)

Describe any pattern you see in the results. Relate your findings to what we discussed during lectures. Include data to justify your findings.


*ADD YOUR FINDINGS HERE*

## Part 4: Reflection (2 marks)
Include a sentence or two about:
- what you liked or disliked,
- found interesting, confusing, challangeing, motivating
while working on this assignment.


*ADD YOUR THOUGHTS HERE*

## Part 5: Bonus Question (3 marks)

Repeat Part 2 and compare the support vector machines model used to `LinearSVC(max_iter=5000)`. Does using `LinearSVC` improve the results? Why or why not?

Is `LinearSVC` a good fit for this dataset? Why or why not?

In [27]:
# TO DO: ADD YOUR CODE HERE

*ANSWER HERE*